In [3]:
from flygym.mujoco import Parameters, NeuroMechFly

from flygym.mujoco.examples.common import PreprogrammedSteps
import numpy as np

from flygym.mujoco.preprogrammed import all_leg_dofs

import matplotlib.pyplot as plt
from gymnasium.utils.env_checker import check_env

# Mouvent de grouping

In [4]:
import matplotlib.pyplot as plt

# Assuming `legs`, `preprogrammed_steps`, `swing_periods`, `nmf`, `sim_params`, `run_time`, and `adhesion_action` are defined

nmf = NeuroMechFly(Parameters(enable_adhesion=True, draw_adhesion=True))


preprogrammed_steps = PreprogrammedSteps()
swing_periods = preprogrammed_steps.swing_period
legs = preprogrammed_steps.legs

adhesion_action= np.zeros(len(legs))
# Initialize standing action using preprogrammed steps for all legs
standing_action = []
for leg in legs:
    standing_action.extend(
        preprogrammed_steps.get_joint_angles(leg, swing_periods[leg][1])
    )

print(standing_action[nmf.actuated_joints.index("joint_LHCoxa")],)
stand_action = {"joints": standing_action, "adhesion": adhesion_action}

# Let the fly stand on the floor first
for i in range(int(0.2 // nmf.timestep)):
    nmf.step(stand_action)

# Debug print
print("Standing action:", standing_action)
print("Actuated joints:", nmf.actuated_joints)

run_time1 =0.2
run_time2 =0.5

sim_params = Parameters(
    timestep=1e-4,
    render_mode="saved",
    render_playspeed=0.5,
    render_window_size=(800, 608),
    enable_olfaction=True,
    enable_adhesion=True,
    draw_adhesion=False,
    render_camera="Animat/camera_right",
)

# Simulation parameters
timestep = sim_params.timestep
target_num_steps1 = int(run_time1 / timestep)
target_num_steps2 = int(run_time2 / timestep)

# Define group actions for the specific joints
group_action = {
    "joint_LMTibia": np.linspace(standing_action[nmf.actuated_joints.index("joint_LMTibia")], 2.60, target_num_steps1),
    "joint_RMTibia": np.linspace(standing_action[nmf.actuated_joints.index("joint_RMTibia")], 2.60, target_num_steps1),
    "joint_LMTarsus1": np.linspace(standing_action[nmf.actuated_joints.index("joint_LMTarsus1")], -1.6, target_num_steps1),
    "joint_RMTarsus1": np.linspace(standing_action[nmf.actuated_joints.index("joint_RMTarsus1")], -1.6, target_num_steps1),
    "joint_LHTarsus1": np.linspace(standing_action[nmf.actuated_joints.index("joint_LHTarsus1")], -1, target_num_steps1),
    "joint_RHTarsus1": np.linspace(standing_action[nmf.actuated_joints.index("joint_RHTarsus1")], -1, target_num_steps1),
    "joint_LHCoxa": np.linspace(standing_action[nmf.actuated_joints.index("joint_LHCoxa")], 0.2, target_num_steps1),
    "joint_RHCoxa": np.linspace(standing_action[nmf.actuated_joints.index("joint_RHCoxa")], 0.2, target_num_steps1),
    "joint_LHTibia": np.linspace(standing_action[nmf.actuated_joints.index("joint_LHTibia")], standing_action[nmf.actuated_joints.index("joint_LHTibia")], target_num_steps1),
    "joint_RHTibia": np.linspace(standing_action[nmf.actuated_joints.index("joint_RHTibia")], standing_action[nmf.actuated_joints.index("joint_RHTibia")], target_num_steps1)
}

#defin the action for the jump
jumps_action = {
    "joint_LMTibia": np.linspace(2.60, 0, target_num_steps2),
    "joint_RMTibia": np.linspace(2.60, 0, target_num_steps2),
    "joint_LMTarsus1": np.linspace(-1.6, 0, target_num_steps2),
    "joint_RMTarsus1": np.linspace(-1.6, 0, target_num_steps2),
    "joint_LHTarsus1": np.linspace(-1, 0, target_num_steps2),
    "joint_RHTarsus1": np.linspace(-1, 0, target_num_steps2),
    "joint_LHCoxa": np.linspace(0.2, 0, target_num_steps2),
    "joint_RHCoxa": np.linspace(0.2, 0, target_num_steps2),
    "joint_LHTibia": np.linspace(standing_action[nmf.actuated_joints.index("joint_LHTibia")], 1.5,target_num_steps2),
    "joint_RHTibia": np.linspace(standing_action[nmf.actuated_joints.index("joint_RHTibia")], 1.5,target_num_steps2)

}

# Actuated joints and data block initialization
actuated_joints = ["joint_LMTibia", "joint_RMTibia", "joint_LMTarsus1", "joint_RMTarsus1" ,"joint_LHTarsus1", "joint_RHTarsus1","joint_LHCoxa", "joint_RHCoxa", "joint_LHTibia", "joint_RHTibia"]
data_block1 = np.zeros((len(actuated_joints), target_num_steps1))
output_t1 = np.arange(target_num_steps1) * timestep
input_t1 = np.linspace(0, timestep * (target_num_steps1 - 1), num=target_num_steps1)

data_block2 = np.zeros((len(actuated_joints), target_num_steps2))
output_t2 = np.arange(target_num_steps2) * timestep
input_t2 = np.linspace(0, timestep * (target_num_steps2 - 1), num=target_num_steps2)


# Interpolation for the specified joints
for i, joint in enumerate(actuated_joints):
    data_block1[i, :] = np.interp(output_t1, input_t1, np.array(group_action[joint]))

for i, joint in enumerate(actuated_joints):
    data_block2[i, :] = np.interp(output_t2, input_t2, np.array(jumps_action[joint]))


# Get the total number of actuated joints
total_actuated_joints = len(nmf.actuated_joints)

# Lists to store joint angle values for plotting
joint_LMTibia_values = []
joint_RMTibia_values = []
joint_LMTarsus_values = []
joint_RMTarsus_values = []
joint_LHTarsus_values = []
joint_RHTarsus_values = []
joint_LHCoxa_values = []
joint_RHCoxa_values = []
joint_LHTibia_values = []
joint_RHTibia_values = []

joint_angles=standing_action.copy()

# Main loop to update joint angles and perform actions
for i in range(target_num_steps1):
    # Update specific joints with interpolated values
    joint_angles[nmf.actuated_joints.index("joint_LMTibia")] = data_block1[0, i]
    joint_angles[nmf.actuated_joints.index("joint_RMTibia")] = data_block1[1, i]
    joint_angles[nmf.actuated_joints.index("joint_LMTarsus1")] = data_block1[2, i]
    joint_angles[nmf.actuated_joints.index("joint_RMTarsus1")] = data_block1[3, i]
    joint_angles[nmf.actuated_joints.index("joint_LHTarsus1")] = data_block1[4, i]
    joint_angles[nmf.actuated_joints.index("joint_RHTarsus1")] = data_block1[5, i]    
    joint_angles[nmf.actuated_joints.index("joint_LHCoxa")] = data_block1[6, i]
    joint_angles[nmf.actuated_joints.index("joint_RHCoxa")] = data_block1[7, i]
    joint_angles[nmf.actuated_joints.index("joint_LHTibia")] = data_block1[8, i]
    joint_angles[nmf.actuated_joints.index("joint_RHTibia")] = data_block1[9, i]

    # Store values for plotting
    joint_LMTibia_values.append(data_block1[0, i])
    joint_RMTibia_values.append(data_block1[1, i])
    joint_LMTarsus_values.append(data_block1[2, i])
    joint_RMTarsus_values.append(data_block1[3, i])
    joint_LHTarsus_values.append(data_block1[4, i])
    joint_RHTarsus_values.append(data_block1[5, i])
    joint_LHCoxa_values.append(data_block1[6, i])
    joint_RHCoxa_values.append(data_block1[7, i])
    joint_LHTibia_values.append(data_block1[8, i])
    joint_RHTibia_values.append(data_block1[9, i])

    print(joint_angles)
    action = {"joints": joint_angles, "adhesion": adhesion_action}

    # Debug print for action
    #print(f"Action at step {i}: {action}")

    nmf.step(action)
    nmf.render()

for i in range (target_num_steps2):
    if i < (target_num_steps2 - 2000):
        # If it's the last iteration, suppress adhesion
        adhesion_action = np.ones(len(legs))
    else:
        # Otherwise, keep adhesion enabled
        adhesion_action = np.zeros(len(legs))
        # Update specific joints with interpolated values
        
    joint_angles[nmf.actuated_joints.index("joint_LMTibia")] = data_block2[0, i]
    joint_angles[nmf.actuated_joints.index("joint_RMTibia")] = data_block2[1, i]
    joint_angles[nmf.actuated_joints.index("joint_LMTarsus1")] = data_block2[2, i]
    joint_angles[nmf.actuated_joints.index("joint_RMTarsus1")] = data_block2[3, i]
    joint_angles[nmf.actuated_joints.index("joint_LHTarsus1")] = data_block2[4, i]
    joint_angles[nmf.actuated_joints.index("joint_RHTarsus1")] = data_block2[5, i]   
    joint_angles[nmf.actuated_joints.index("joint_LHCoxa")] = data_block2[6, i]
    joint_angles[nmf.actuated_joints.index("joint_RHCoxa")] = data_block2[7, i]
    joint_angles[nmf.actuated_joints.index("joint_LHTibia")] = data_block2[8, i]
    joint_angles[nmf.actuated_joints.index("joint_RHTibia")] = data_block2[9, i]

    # Store values for plotting
    joint_LMTibia_values.append(data_block2[0, i])
    joint_RMTibia_values.append(data_block2[1, i])
    joint_LMTarsus_values.append(data_block2[2, i])
    joint_RMTarsus_values.append(data_block2[3, i])
    joint_LHTarsus_values.append(data_block2[4, i])
    joint_RHTarsus_values.append(data_block2[5, i])
    joint_LHCoxa_values.append(data_block2[6, i])
    joint_RHCoxa_values.append(data_block2[7, i])
    joint_LHTibia_values.append(data_block2[8, i])
    joint_RHTibia_values.append(data_block2[9, i])
    
    print(joint_angles)
    action = {"joints": joint_angles, "adhesion": adhesion_action}

    # Debug print for action
    #print(f"Action at step {i}: {action}")

    nmf.step(action)
    nmf.render()


nmf.save_video('linspace.mp4')

from IPython.display import Video
Video('linspace.mp4', width=800, height=608)



0.3107808864416293
Standing action: [-0.17807922664387055, 0.4355319917867498, -0.1375207099199162, -1.6154024071852708, 0.15835333925815945, 0.7649009042357457, 0.10346736143929347, 0.002788572101382972, 1.270125282727024, -0.026239472431583945, -1.7484030407291498, 0.5099974114646831, 1.3874909352037004, -0.5220701145664404, 0.3107808864416293, 2.230334786406371, 0.06210684744833214, -2.4530385318647285, 0.028191723119268715, 2.4635586103152844, -0.7233521339746135, -0.17807922664387055, -0.4355319917867498, 0.1375207099199162, -1.6154024071852708, -0.15835333925815945, 0.7649009042357457, 0.10346736143929347, 0.002788572101382972, -1.270125282727024, 0.026239472431583945, -1.7484030407291498, -0.5099974114646831, 1.3874909352037004, -0.5220701145664404, 0.3107808864416293, -2.230334786406371, -0.06210684744833214, -2.4530385318647285, -0.028191723119268715, 2.4635586103152844, -0.7233521339746135]
Actuated joints: ['joint_LFCoxa', 'joint_LFCoxa_roll', 'joint_LFCoxa_yaw', 'joint_LFFe

In [ ]:
# Plotting the joint angles
plt.figure(figsize=(10, 6))
plt.plot(output_t, joint_LMTibia_values, label='Joint LMTibia')
plt.plot(output_t, joint_RMTibia_values, label='Joint RMTibia')
plt.xlabel('Time (seconds)')
plt.ylabel('Joint Angle (radians)')
plt.title('Joint Angle Variation Over Time')
plt.legend()
plt.grid(True)
plt.show()